In [ ]:
import obspy as op
import numpy as np
import cartopy.crs as ccrs
from obspy.clients.fdsn import Client
import cartopy.feature as cfeature
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from obspy import UTCDateTime
from IPython.display import HTML



client = Client("IRIS")
t1 = op.UTCDateTime("1972-01-01T00:00:00") #start time of the request
t2 = op.UTCDateTime("2023-10-31T00:00:00")


minLat = 39.63743199569635
maxLat = 51.22510685737506
minLon = -128.92965238491036
maxLon =  -122.53874193108292
minMag = 5.0

catalog = client.get_events(starttime=t1, endtime=t2,  minlatitude=minLat,         
maxlatitude=maxLat, minlongitude=minLon, maxlongitude=maxLon, 
minmagnitude=minMag)

plt.rcParams['figure.figsize'] = [15, 7]
catalog.plot(projection='local')
    


In [ ]:
print(len(catalog.events))
print(catalog[0].origins[0].latitude,catalog[0].origins[0].longitude)
print(catalog[0].origins[0].time)
print(catalog[0].magnitudes[0].mag)

In [ ]:
# function to fetch earthquake data for a specific year
def get_earthquake_data(year):
    t1 = UTCDateTime(f"{year}-01-01T00:00:00")
    t2 = UTCDateTime(f"{year + 1}-01-01T00:00:00")
    
    minLat, maxLat, minLon, maxLon = 39.63743199569635, 51.22510685737506, -128.92965238491036, -122.53874193108292
    minMag = 4.0

    client = Client("IRIS")
    catalog = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
                                minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)
    return catalog

# set up the figure and axis with a map background
fig, ax = plt.subplots(figsize=(10, 6), subplot_kw={'projection': ccrs.PlateCarree()})
ax.set_title('Earthquakes Over the Years')
ax.set_xlim(-130, -120)
ax.set_ylim(40, 52)
ax.coastlines(resolution='10m', color='gray')
ax.gridlines(draw_labels=True)

# create empty scatter plot
sc = ax.scatter([], [])

# specify year for each frame
year_text = ax.text(0.95, 0.95, '', transform=ax.transAxes, ha='right', va='top', fontsize=12, backgroundcolor='w')

# function for updating the scatter plot and text annotation for each frame
def update(frame):
    year = frame + 1972  # Adjust the starting year
    data = get_earthquake_data(year)
    # Extract latitude, longitude, magnitude, and depth for each earthquake
    lat_lon_mag_dep = [
        (event.origins[-1].longitude, event.origins[-1].latitude, event.magnitudes[0].mag, event.origins[0].depth / 1000.0)
        for event in data
    ]
    lons, lats, mags, depths = zip(*lat_lon_mag_dep)
    
    # update scatter plot with new earthquake data
    sc.set_offsets(list(zip(lons, lats)))
    
    # adjust the size of the markers based on earthquake magnitudes
    sc.set_sizes(np.array(mags) ** 4)
    
    # set colors based on depths
    sc.set_array(np.array(depths))
    
    # update year
    year_text.set_text(f'Year: {year}')

# create the animation

ani = animation.FuncAnimation(fig, update, frames=range(0, 2023 - 1972), interval=500, blit=False)

# create a colorbar for depth
cbar = plt.colorbar(sc, ax=ax, orientation='vertical', pad=0.1)
cbar.set_label('Depth [km]', fontsize=12)

# save the animation as a video using PillowWriter
ani.save('earthquake_animation.gif', writer='pillow', fps=2)

# display the animation
HTML(ani.to_jshtml())


In [ ]:
ani.save('earthquake_animation.mp4', writer='ffmpeg', fps=2)